In [58]:
import pandas as pd
import numpy as np
from sklearn.model_selection import train_test_split
from lightgbm import LGBMClassifier
from sklearn.metrics import accuracy_score, classification_report
from sklearn.model_selection import RandomizedSearchCV
from sklearn.model_selection import cross_val_score


In [59]:
# データの読み込み
train = pd.read_csv('../../data/train.csv')
test = pd.read_csv('../../data/test.csv')

# 特徴量とターゲット変数の分割
X_train = train.drop('dengue', axis=1)  
y_train = train['dengue']

X_test = test.drop('dengue', axis=1)  
y_test = test['dengue']


In [60]:
model = LGBMClassifier(class_weight='balanced',)


In [61]:
param_dist = {
    'num_leaves': np.arange(380,400, 1),
    'learning_rate': np.logspace(-0.02, 0, 10),
    'n_estimators': np.arange(240, 280, 1),
    'max_depth': np.arange(3, 15, 1),
    'lambda_l2' :np.arange(0.00001,0.00005,10)
}

In [62]:
random_search = RandomizedSearchCV(
    estimator=model,
    param_distributions=param_dist,
    n_iter=50,  # 試行回数
    scoring='accuracy',  # 評価指標
    cv=5,  # クロスバリデーション
    verbose=1,
    random_state=42
)


In [63]:
# X_train, y_trainは学習データとラベル
random_search.fit(X_train, y_train)

Fitting 5 folds for each of 50 candidates, totalling 250 fits
[LightGBM] [Warning] lambda_l2 is set=1e-05, reg_lambda=0.0 will be ignored. Current value: lambda_l2=1e-05
[LightGBM] [Warning] Found whitespace in feature_names, replace with underlines
[LightGBM] [Warning] lambda_l2 is set=1e-05, reg_lambda=0.0 will be ignored. Current value: lambda_l2=1e-05
[LightGBM] [Info] Number of positive: 2860, number of negative: 3244
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.031738 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 26
[LightGBM] [Info] Number of data points in the train set: 6104, number of used features: 13
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.500000 -> initscore=-0.000000
[LightGBM] [Info] Start training from score -0.000000
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Wa

RandomizedSearchCV(cv=5, estimator=LGBMClassifier(class_weight='balanced'),
                   n_iter=50,
                   param_distributions={'lambda_l2': array([1.e-05]),
                                        'learning_rate': array([0.95499259, 0.95989167, 0.96481588, 0.96976536, 0.97474023,
       0.97974061, 0.98476665, 0.98981847, 0.99489621, 1.        ]),
                                        'max_depth': array([ 3,  4,  5,  6,  7,  8,  9, 10, 11, 12, 13, 14]),
                                        'n_estimators': array([240, 241, 242, 243, 244, 245, 246, 247, 248, 249, 250, 251, 252,
       253, 254, 255, 256, 257, 258, 259, 260, 261, 262, 263, 264, 265,
       266, 267, 268, 269, 270, 271, 272, 273, 274, 275, 276, 277, 278,
       279]),
                                        'num_leaves': array([380, 381, 382, 383, 384, 385, 386, 387, 388, 389, 390, 391, 392,
       393, 394, 395, 396, 397, 398, 399])},
                   random_state=42, scoring='accuracy', verbose=1)

In [64]:
print("Best Parameters: ", random_search.best_params_)

Best Parameters:  {'num_leaves': np.int64(383), 'n_estimators': np.int64(253), 'max_depth': np.int64(6), 'learning_rate': np.float64(0.9847666521101581), 'lambda_l2': np.float64(1e-05)}


In [65]:
model = LGBMClassifier(**random_search.best_params_)
model.fit(X_train, y_train)
#model.booster_.save_model('optimized_LGBM_random.txt')

[LightGBM] [Warning] lambda_l2 is set=1e-05, reg_lambda=0.0 will be ignored. Current value: lambda_l2=1e-05
[LightGBM] [Warning] Found whitespace in feature_names, replace with underlines
[LightGBM] [Warning] lambda_l2 is set=1e-05, reg_lambda=0.0 will be ignored. Current value: lambda_l2=1e-05
[LightGBM] [Info] Number of positive: 3575, number of negative: 4056
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.016882 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 26
[LightGBM] [Info] Number of data points in the train set: 7631, number of used features: 13
[LightGBM] [Info] [binary:BoostFromScore]: pavg=0.468484 -> initscore=-0.126232
[LightGBM] [Info] Start training from score -0.126232
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[

LGBMClassifier(lambda_l2=np.float64(1e-05),
               learning_rate=np.float64(0.9847666521101581),
               max_depth=np.int64(6), n_estimators=np.int64(253),
               num_leaves=np.int64(383))

In [66]:
# テストデータを使って予測
y_pred = model.predict(X_test)

# 精度の評価
accuracy = accuracy_score(y_test, y_pred)
print(f'Accuracy: {accuracy}')

# 分類レポートの表示
print(classification_report(y_test, y_pred))

[LightGBM] [Warning] lambda_l2 is set=1e-05, reg_lambda=0.0 will be ignored. Current value: lambda_l2=1e-05
Accuracy: 0.5458689458689459
              precision    recall  f1-score   support

           0       0.68      0.58      0.63      1157
           1       0.37      0.48      0.42       598

    accuracy                           0.55      1755
   macro avg       0.53      0.53      0.52      1755
weighted avg       0.58      0.55      0.56      1755

